# **Desafio Alfabeto Alienígena**

## IESB - Pós Graduação em Inteligência Artificial

## Aprendizado não supervisionado - Prof: Paulo Cotta

#### Data de entrega: 21/10/2019

### **Nome do aluno:**

O IESB, juntamente com o programa aeroespacial da Agência NASTESB, estão investigando uma nave espacial que veio de outro planeta. Espalhadas dentro da nave foram encontradas várias letras.

Um grupo de cientistas do própria IESB encontrou um padrão com a linguagem muito similar à Suméria e começou a decifrar, mas todos os cientistas foram abduzidos e agora, para saber onde os cientistas foram e descobrir qual civilização os abduziu, devem terminar de decifrar as imagens das letras.

In [1]:
import tensorflow as tf; 
from PIL import Image, ImageFilter
import os
import cv2 as cv
from random import randint
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import functools
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix
from mlxtend.plotting import plot_confusion_matrix
from sklearn.metrics import accuracy_score
import random
from scipy import ndarray
import skimage as sk
from skimage import transform
from skimage import util

Será apresentado, neste momento, o DataSet do alfabeto atual nosso:

In [ ]:
for name in os.listdir('./dataset/alfabeto'):
    path = './dataset/alfabeto/' + name
    print(path)
    image = Image.open(path)
    image.show()

Agora será apresentado o DataSet do alfabeto baseado em Sumério, mas que não foi descoberto ainda qual é a língua exata. O mesmo foi encontrado na nave alienígena:

In [ ]:
for name in os.listdir('./dataset/sumerio'):
    path = './dataset/sumerio/' + name
    print(path)
    image = Image.open(path)
    image.show()

Os pesquisadores, ao realizarem seus estudos antes de serem abdusidos, também identificaram alguns dados que nos mostram o padrão DE <==> PARA entre a nossa linguagem e a linguagem encontrada:

In [ ]:
for name in os.listdir('./dataset/encontrado'):
    path = './dataset/encontrado/' + name
    print(path)
    image = Image.open(path)
    image.show()

**Primeiro exercício: **

Conforme apresentado na primeira aula de aprendizado não supervisionado, deve-se clusterizar os dados e tentar encontrar um padrão nos desenhos, utilizando a sua própria dedução.

E, de acordo com o que foi encontrado, devemos decifrar o restante do alfabeto. Para decifrar o restante do alfabeto, tenha em mente que:

Se o alfabeto contém 26 letras e os números contém de 0 a 9, sendo o 0 neutro, devemos contabilizar então que temos 9 números, agora devemos identificar as letras faltantes para identificar o texto que será apresentado na questão três. 

**Dica:**
- De A a Z e de 0 a 9, deve-se descobrir letra a letra.

É obrigatório representar a forma que foi descoberto o alfabeto alienígena por você, pesquisador, em formato de código fonte. 

Exemplo: apresentar gráfico dos clusters identificados utilizando o matplotlib e demonstrar o DE e PARA de cada letra e número do nosso alfabeto com o alfabeto alienigena.

In [2]:
path_sumerio = "./dataset/sumerio/"
path_alfabeto = "./dataset/alfabeto/"

In [3]:
### Deve-se colocar o código aqui
caracteres = ['A', 'B', 'C','D','E','F','G','H','I','J','K','L','M','N','O','P','Q','R','S','T','U','V','W','X','Y','Z', '0']
de_para = {}
for nomeCompleto in os.listdir(path_sumerio):
    nomeArquivo = nomeCompleto[: nomeCompleto.rfind('.')]
    if(nomeArquivo[0] == '_' and len(nomeArquivo) > 1 and nomeArquivo[1] == '!'):
        #número
        numero = len(nomeArquivo) - 1
        de_para[str(numero)] = nomeArquivo
    else :
        multiplicador = 0                # primeiro grupo
        if(nomeArquivo[0] == '!'):
            multiplicador = 1            #segundo grupo
        elif nomeArquivo[0] == '#':
            multiplicador = 2            #terceiro grupo
        posicao = (len(nomeArquivo) - 1) + 9 * multiplicador
        caractere = caracteres[posicao]
        de_para[caractere] = nomeArquivo

In [4]:
for caractere, nomeArquivo in sorted(de_para.items()): 
    print(caractere, ":", nomeArquivo) 

0 : #########
1 : _!
2 : _!!
3 : _!!!
4 : _!!!!
5 : _!!!!!
6 : _!!!!!!
7 : _!!!!!!!
8 : _!!!!!!!!
9 : _!!!!!!!!!
A : _
B : __
C : ___
D : ____
E : _____
F : ______
G : _______
H : ________
I : _________
J : !
K : !!
L : !!!
M : !!!!
N : !!!!!
O : !!!!!!
P : !!!!!!!
Q : !!!!!!!!
R : !!!!!!!!!
S : #
T : ##
U : ###
V : ####
W : #####
X : ######
Y : #######
Z : ########


In [5]:
def getPaginas(tamanho_pagina):
    chaves_ordenadas = sorted(de_para.keys())
    paginas = []
    quantidade_paginas = int(len(chaves_ordenadas)/tamanho_pagina)
    for i in range(quantidade_paginas):
        inicio = i * tamanho_pagina
        fim = (i+1) * tamanho_pagina
        paginas.append(chaves_ordenadas[inicio:fim])
    return paginas

In [6]:
tamanho_pagina = 9
paginas = getPaginas(tamanho_pagina)
linhas = len(paginas) * 2
colunas = len(paginas[0])

fig, axs = plt.subplots(linhas, colunas, figsize=(300, 300))
fig.suptitle('Conversão do alfabeto romano para o alfabeto sumério', fontsize=500)

for coluna in range(tamanho_pagina):
    for linha in range(len(paginas)):
        caractere =  paginas[linha][coluna]
        nome_arquivo_alfabeto = path_alfabeto + caractere + ".png"
        nome_arquivo_sumerio = path_sumerio + de_para[caractere] + ".png"
        
        imagemAlfabeto = cv.imread(nome_arquivo_alfabeto)
        imagemSumerio = cv.imread(nome_arquivo_sumerio)

        axs[linha * 2, coluna].imshow(imagemAlfabeto)
        axs[linha * 2 + 1, coluna].imshow(imagemSumerio)
plt.show()

Após identificar, deve-se explicar qual foi a técnica e a lógica que foi utilizada.

**Explicar aqui**

O primeiro passo foi criar uma matriz com 12 linhas e 3 colunas de forma a comportar as 26 letras, os 9 números e o zero.
Preenchi as células com os símbolos identificados pelos cientistas, iniciando pelos números de 1 a 9 e depois pelas letras de A a Z e por último o zero.

Com a matriz preenchida com os símboloss já identificados, percebi que o padrão da primeira coluna é sempre repetido 2 vezes na segunda e 3 vezes na terceira coluna, por exemplo se na primeira coluna há uma barra vertical, na segunda serão 2 barras e na terceira serão 3 barras.

Para os números, havia um símbolo identificado em cada uma das 3 linhas, o 2, o 5 e o 8 (todos na segunda coluna). Para completar a primeira coluna dessas linhas removi uma barra vertical na primeira linha e uma barra horizontal na segunda e terceira linhas. Para completar a terceira coluna, acrescentei uma barra vertical na primeira linha e uma barra horizontal na segunda e terceira linhas.

Para as letras, os símbolos identificados estavam espalhados na tabela. Havia síbolos na primeira, segunda e terceira colunas. 

Quando o símbolo identificado estava na primeira coluna (A, J, S e V) repetia o padrão 1 vez na segunda coluna e 2 vezes na terceira coluna.

Quando o símbolo identificado estava na segunda coluna (H, N e Q) identificava o que estava duplicado no símbolo, removia a duplicação e aplicava na primeira coluna; na terceira coluna acrescentava mais uma característica do que estava duplicado na segunda coluna.

Quando o símbolo identificado estava na terceira coluna (F) identificava a característica que estava triplicada no símbolo, removia uma das características e aplicava na segunda coluna e removia mais uma característica e aplicava na primeira coluna.

Após seguir esse procedimento, ficou faltando completar a última linha (Y e Z), que não tinha nenhum símbolo identificado para ela. Para identificar esses símbolos, recorri ao padrão de nome dos arquivos conforme explicado a seguir.

Após a identificação do padrão das imagens, percebi que havia uma padronização nos nomes dos arquivos também:<br>
1) Os arquivos correspondentes aos números (1 a 9) começam com '?' (no caso do Windows, '_') seguido de caracteres '!' onde a quantidade de caracteres '!' diz qual o número correspondente. Por exemplo, '?!' é o número 1 e '?!!!' é o número 3.<br>
2)Percebi que os caracteres restantes estão agrupados de 9 em 9, seguindo as seguintes regras:<br>
- O primeiro grupo tem os nomes de arquivos somente com '?' (no caso do Windows '_'). Nesse grupo estão as letras A-I. Por exemplo, '?' corresponde ao 'A' e '????' corresponde ao 'D'.<br> 
- O Segundo grupo tem os arquivos com o nome formado exclusivamente por '!'. Aqui estão as letras J-R. Por exempo, '!' corresponde ao 'J' e '!!!' corresponde ao 'L'.<br>
- O terceiro e último grupo são os que tem o nome formado exclusivamente por '#'. Nesse grupo estão as letras S-Z e o número zero. Por exemplo, '#' corresponde à letra 'S' e '#########' corresponde ao zero.





**Segundo exercício:**

Utilize um KNN (algoritmo de vizinhos próximos) para classificar os rótulos que você criou para os clusters do exercício I. Lembrando que deve efetuar a separação de dados para testar e validar as informações. 

**Dicas:**

- Faça um Data Augumentation.
- Faça padding centralizando o conteúdo das imagens para padronizá-las para o mesmo tamanho.

In [7]:
def getImagem(imageName):
    return cv.imread(imageName, cv.IMREAD_REDUCED_GRAYSCALE_2)

In [8]:
def getImagemComBorda(imagem):
    
    borderType = cv.BORDER_CONSTANT
    
    top = int(0.05 * imagem.shape[0])  # shape[0] = rows
    bottom = top
    left = int(0.05 * imagem.shape[1])  # shape[1] = cols
    right = left
    
    value = [randint(0, 255), randint(0, 255), randint(0, 255)]
        
    return cv.copyMakeBorder(imagem, top, bottom, left, right, borderType, None, value)    

In [9]:
def getImagemNormalizada(imagem, dim):
    return cv.resize(imagem, dim)

In [10]:
def getImagemRotacionada(imagem):
    random_degree = random.uniform(-25,25)
    return sk.transform.rotate(imagem, random_degree)

# Normalização das Imagens

Cálculo da média das dimensões das imagens do alfabeto sumério:

In [11]:
mediaAltura = 0
mediaLargura = 0
for caractere, nomeArquivo in sorted(de_para.items()): 
    nome_arquivo_sumerio = path_sumerio + de_para[caractere] + ".png"
    imagemOriginal = getImagem(nome_arquivo_sumerio)
    mediaLargura += imagemOriginal.shape[0]
    mediaAltura += imagemOriginal.shape[1]
mediaLargura = int(round(mediaLargura/ len(de_para), 0))
mediaAltura = int(round(mediaAltura/len(de_para), 0))

dimensao_padrao = (mediaLargura, mediaAltura)
print(dimensao_padrao)

(29, 27)


In [12]:
quantidade_transformacoes = 2
tamanho_pagina = 9
paginas = getPaginas(tamanho_pagina)
linhas = len(paginas) * quantidade_transformacoes
colunas = len(paginas[0])

fig, axs = plt.subplots(linhas, colunas, figsize=(300, 300))
fig.suptitle('Normalização das imagens do alfabeto sumério', fontsize=300)

for coluna in range(tamanho_pagina):
    for linha in range(len(paginas)):
        caractere =  paginas[linha][coluna]
        nome_arquivo_sumerio = path_sumerio + de_para[caractere] + ".png"

        imagemOriginal = getImagem(nome_arquivo_sumerio)
        imagemNormalizada = getImagemNormalizada(imagemOriginal, dimensao_padrao)
        
        axs[linha * quantidade_transformacoes, coluna].imshow(imagemOriginal)
        axs[linha * quantidade_transformacoes + 1, coluna].imshow(imagemNormalizada)
plt.show() 

In [13]:
def getImagemTratada(imagemOriginal):
    #imagemTratada = getImagemComBorda(imagemOriginal)
    #imagemTratada = getImagemNormalizada(imagemTratada, dimensao_padrao)
    #return imagemTratada
    
    imagemTratada = getImagemNormalizada(imagemOriginal, dimensao_padrao)
    return imagemTratada

Construção do dataset composto das imagens do alfabeto sumério adicionadas de imagens rotacionadas das mesmas.

In [14]:
caracteristicas = []
targets = []
for caractere, nomeArquivo in sorted(de_para.items()): 
    nome_arquivo_sumerio = path_sumerio + de_para[caractere] + ".png" 
    imagemOriginal = getImagem(nome_arquivo_sumerio)
    
    #adiciona a imagem original:
    imagemOriginalTratada = getImagemTratada(imagemOriginal)
    caracteristicas.append(imagemOriginalTratada.flatten())
    targets.append(caractere)
   
    for i in range(90):
        #adiciona as imagens rotacionadas:
        imagemRotacionada = getImagemRotacionada(imagemOriginal)
        imagemRotacionada = getImagemTratada(imagemRotacionada)

        caracteristicas.append(imagemRotacionada.flatten())
        targets.append(caractere)
        
dados = [targets, caracteristicas]    
df = pd.DataFrame(data = caracteristicas)
df.insert(0, "target", targets, True)

Características do dataset construído:

In [15]:
df.shape

(3276, 784)

In [16]:
df.head()

target           0           1           2           3           4  \
0      0  255.000000  255.000000  255.000000  255.000000  255.000000   
1      0    0.000000    0.000000    0.056248    0.229321    0.702965   
2      0    0.151278    0.201659    0.266666    0.331673    0.396680   
3      0    0.215901    0.262240    0.322032    0.381824    0.441616   
4      0    0.000000    0.000000    0.000000    0.000000    0.000000   

            5           6           7           8  ...         773  \
0  255.000000  255.000000  255.000000  255.000000  ...  255.000000   
1    1.000000    1.000000    1.000000    1.000000  ...    1.000000   
2    0.461687    0.526694    0.591701    0.656708  ...    0.721715   
3    0.501408    0.561200    0.620992    0.680784  ...    0.740576   
4    0.000000    0.000000    0.060329    0.216077  ...    0.456757   

          774         775         776         777         778         779  \
0  255.000000  255.000000  255.000000  255.000000  255.000000  255.000000   
1    1.000000    1.000000    1.000000    1.000000    0.702965    0.229321   
2    0.656708    0.591701    0.526694    0.461687    0.396680    0.331673   
3    0.680784    0.620992    0.561200    0.501408    0.441616    0.381824   
4    0.216077    0.060329    0.000000    0.000000    0.000000    0.000000   

          780         781         782  
0  255.000000  255.000000  255.000000  
1    0.056248    0.000000    0.000000  
2    0.266666    0.201659    0.151278  
3    0.322032    0.262240    0.215901  
4    0.000000    0.000000    0.000000  

[5 rows x 784 columns]

Particionamento dos dados em treinamento e teste:

In [17]:
X = df.iloc[:,1:].values
Y = df.iloc[:,:1].values
X_treino, X_teste, Y_treino, Y_teste = train_test_split(X, Y, test_size=.20)

print(len(X_treino), len(Y_treino), len(X_teste), len(Y_teste))

2620 2620 656 656


Treinamento do KNN:

In [18]:
def treinaKNN(k, p, X_treino, Y_treino, X_teste, Y_teste):
    classificador = KNeighborsClassifier(n_neighbors=k, p=p)
    classificador.fit(X_treino, Y_treino.ravel())
    return  classificador.predict(X_teste)

In [19]:
Y_pred = treinaKNN(3,2, X_treino, Y_treino, X_teste, Y_teste)

Acurácia:

In [20]:
acuracia = accuracy_score(Y_teste, Y_pred)
print(acuracia)

0.9908536585365854


"Matriz de confusão"

In [21]:
for i in list(zip(Y_teste, Y_pred)):
    print(i[0][0], i[1], i[0][0]== str(i[1]))

S S True
L L True
T T True
A A True
F F True
0 0 True
L L True
Y Y True
B B True
P P True
T T True
E E True
I I True
C C True
K K True
8 8 True
8 8 True
3 3 True
Z Z True
U U True
P P True
G G True
Q Q True
2 2 True
2 2 True
5 5 True
V V True
V V True
Z Z True
K K True
L L True
X X True
Y Y True
A A True
I I True
L L True
Y Y True
Q Q True
V V True
S S True
4 4 True
C C True
E E True
2 2 True
Z Z True
5 5 True
K K True
1 1 True
9 9 True
Y Y True
1 1 True
9 9 True
9 9 True
H H True
Q Q True
C C True
Q Q True
D D True
1 1 True
O O True
B B True
R R True
Z Z True
S S True
N N True
U U True
Q Q True
S S True
X X True
U U True
Z Z True
K K True
5 5 True
F F True
5 5 True
Y Y True
0 0 True
2 2 True
A A True
W W True
F F True
R 4 False
D D True
7 7 True
0 0 True
6 6 True
J J True
V V True
N N True
T T True
5 5 True
8 8 True
1 1 True
S S True
3 3 True
X X True
3 3 True
3 3 True
4 4 True
3 3 True
7 7 True
8 8 True
3 3 True
J J True
B B True
W W True
X X True
F F True
C C True
A A True
T T True


**Terceiro Exercício:**

No texto que será apresentado abaixo, seguindo a lógica do primeiro exercício, faça a tradução do mesmo, identificando as imagens, e apresente aqui. Após isso, deve-se transformar o conteúdo que está em imagem para texto, utilizando as labels de cada letra. Se as letras do alfabeto Alienígena não estiverem com as labels certas, deve-se corrigir e, após isso, executar todo o exercício descrito. 


**OBSERVAÇÃO**

Utilize a resposta do exercício I para chegar na resposta desta questão.

In [22]:
path = './dataset/mensagem.png'
image = Image.open(path)
image.show()

In [23]:
enigma = 'O LABORATORIO FOI INVADIDO HELP PLANETA MARTE'.split()
#o número de colunas será o tamanho da maior string do enigma
colunas = len(functools.reduce(lambda x,y : x if len(x) > len(y) else y, enigma))
linhas = len(enigma)

fig, axs = plt.subplots(linhas * 2, colunas, figsize=(300, 300))
fig.suptitle('Enigma desvendado!', fontsize=300)

linha = 0
for palavra in enigma:
    coluna = 0
    for caractere in palavra:
        
        nome_arquivo_alfabeto = path_alfabeto + caractere + ".png"
        nome_arquivo_sumerio = path_sumerio + de_para[caractere] + ".png"
        
        imagemAlfabeto = cv.imread(nome_arquivo_alfabeto)
        imagemSumerio = cv.imread(nome_arquivo_sumerio)

        axs[linha * 2 + 1, coluna].imshow(imagemAlfabeto)
        axs[linha * 2, coluna].imshow(imagemSumerio)
       
        coluna += 1
    linha += 1

plt.title('Enigma desvendado')
plt.show()
